In [6]:
import bs4
import re
from bs4 import BeautifulSoup
import selenium
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import Select
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from time import sleep
import requests
import pandas as pd

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


In [150]:
## 크롬 드라이버 시험 작동

# driver = webdriver.Chrome("/Users/choeunsol/chromedriver_mac64/chromedriver")
# driver.close()

In [28]:
## url 리스트
team_list = ['dbacks', 'braves', 'orioles', 'redsox', 'cubs', 'whitesox', 'reds', 'guardians', 'rockies', 'tigers',
             'astros', 'royals', 'angels', 'dodgers', 'marlins', 'brewers', 'twins', 'mets', 'yankees', 'athletics', 
             'phillies', 'pirates', 'padres', 'mariners', 'giants', 'cardinals', 'rays', 'rangers', 'bluejays', 'nationals']

base = 'https://www.mlb.com/prospects/'

In [7]:
def url_maker(base_url):
    url_mlb_list = []
    for i in range(2014, 2024):
        first_url = base_url + str(i) + '/' + 'braves'
        url_mlb_list.append(first_url)
    return url_mlb_list

# 우리가 긁는 전체 url 생성, 이미 있음
## 근데 2014년 bluejays 같은 경우 망주 랭킹이 없더라.. 이런 부분 확인하고 가야함.

In [8]:
## 드라이버 세팅 (show full list까지)
def driver_setting(url, driver):
    driver.get(url)
    driver.find_element_by_xpath('//*[@id="root"]/div/div/div[3]/div[2]/button').send_keys(Keys.ENTER) 
    # 꼭 show full list 눌러야 작동된다! 6위 아래로는 xpath 바뀜!!
    ## 안 될 경우 sleep sec을 늘려볼 것
    sleep(15)
    return None

In [113]:
def player_info(driver):
    stat_names = driver.find_elements(By.CLASS_NAME, "bio-tab__statName")
    stat_values = driver.find_elements(By.CLASS_NAME, "bio-tab__statValue")
    first_name_element = driver.find_element(By.CLASS_NAME, "top-card__bottom-left-container__first-name")
    last_name_element = driver.find_element(By.CLASS_NAME, "top-card__bottom-left-container__last-name")
    position_element = driver.find_element(By.XPATH, '//*[@id="root"]/div/div/div[3]/div[2]/div[2]/div/div[1]/div[2]/div[3]/span[1]')
    first_name = first_name_element.text
    last_name = last_name_element.text
    position = position_element.text
    scouting_grades_element = driver.find_element(By.XPATH, "//*[@id='root']/div/div/div[3]/div[2]/div[2]/div/div[3]/div/div/p[1]")
    scouting_grades_text = scouting_grades_element.get_attribute("innerHTML")
    scouting_grades = re.sub(r"<.*?>", "", scouting_grades_text).strip().replace("Scouting Grades: ", "")

    data = {
    "first_name": first_name,
    "last_name": last_name,
    "position" : position,
    "Scouting Grades": scouting_grades
    }

    for i in range(len(stat_names)):
        column = stat_names[i].text
        value = stat_values[i].text
        data[column] = value

    # df = pd.DataFrame(data)


    return data

In [93]:
def player_setting(url, driver): # player_info에서 정보 긁어주는 함수
    result_list = []

    if int(url.split('/')[4]) == 2014: # 2014년에는 top20, 그 후로는 top 30
        thr = 20
    else:
        thr = 30

    button = '//*[@id="root"]/div/div/div[3]/table/tbody/tr[1]/td[2]/div/div[2]' # 제일 처음 유망주 체크
    driver.find_element_by_xpath(button).click() # 클릭
    sleep(10) # 대기 (충분히 안 기다려주면 코드 작동 안함)

    for i in range(1, thr+1): # 2014년은 top 20밖에 없음
        try: 
            result = player_info(driver)
            result_list.append(result)
        except:
            print('데이터가 없습니다')
            driver.find_element_by_xpath('//*[@id="root"]/div/div/div[3]/div[2]/div[2]/div/div[4]/button[2]').send_keys(Keys.ENTER)
    
        if i == 1:
            driver.find_element_by_xpath('//*[@id="root"]/div/div/div[3]/div[2]/div[2]/div/div[4]/button').send_keys(Keys.ENTER)
        elif i == thr:
            break
        else:
            try:
                driver.find_element_by_xpath('//*[@id="root"]/div/div/div[3]/div[2]/div[2]/div/div[4]/button[2]').send_keys(Keys.ENTER)
            except:
                print('반복문 오류')
                driver.find_element_by_xpath('//*[@id="root"]/div/div/div[3]/div[2]/div[2]/button').send_keys(Keys.ENTER)
                break

    driver.find_element_by_xpath('//*[@id="root"]/div/div/div[3]/div[2]/div[2]/button').send_keys(Keys.ENTER)
    
    return result_list


In [118]:
## 시험 구동 시 i range 2, j range 2
## 진짜 긁으려면 i range 10, j range 31

def crawling_prospects_info(driver):
    dropdown_year = Select(driver.find_element_by_xpath('//*[@id="root"]/div/div/div[1]/header/div/select'))
    dropdown_team = Select(driver.find_element_by_xpath('/html/body/main/div[2]/div/div/div[2]/nav/ul/li[2]/div/div/select'))
    result_list = []
    for i in reversed(range(10)):
        dropdown_year.select_by_index(i)
        if i == 9:
            base_url = 'https://www.mlb.com/prospects/2014/braves'
        else:
            base_url = 'https://www.mlb.com/prospects/2023/braves'
        for j in range(1, 31):
            dropdown_team.select_by_index(j)
            try:
                wait = WebDriverWait(driver, 10)
                wait.until(EC.element_to_be_clickable((By.XPATH, '//*[@id="root"]/div/div/div[3]/div[2]/button')))
                driver.find_element_by_xpath('//*[@id="root"]/div/div/div[3]/div[2]/button').click()
                l = player_setting(base_url, driver)
                result_list.append(l)
            except:
                current_url = driver.current_url
                print("url : {}의 유망주 정보가 없습니다.".format(current_url))
                continue
    return result_list

In [112]:
## 드라이버 구동
dr = webdriver.Chrome("/Users/choeunsol/chromedriver_mac64/chromedriver")
dr.get('https://www.mlb.com/prospects/2023/braves')

In [115]:
test_list = crawling_prospects_info(dr)

In [119]:
crawling_list = crawling_prospects_info(dr)

데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
데이터가 없습니다
url : https://www.mlb.com/prospects/2014/mets/vic-black-502195의 유망주 정보가 없습니다.
데이터가 없습니다
반복문 오류
데이터가 없습니다
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
url : https://www.mlb.com/prospects/2014/bluejays/의 유망주 정보가 없습니다.
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
데이터가 없습니다
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
url : https://www.mlb.com/prospects/2016/brewers/jacob-barnes-606930의 유망주 정보가 없습니다.
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
url : https://www.mlb.com/prospects/2016/pirates/dario-agrazal-642607의 유망주 정보가 없습니다.
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
반복문 오류
데이터가 없습니다
url : https://www.mlb.com/prospects/2017/tigers/wladimir-pinto-660749의 유망주 정보가 없습니다

In [120]:
crawling_list

[[{'first_name': 'Archie',
   'last_name': 'Bradley',
   'position': 'RHP',
   'Scouting Grades': 'Scouting grades: Fastball: 70 | Curveball: 65 | Changeup: 50 | Control: 50 | Overall: 65',
   'AGE': '30',
   'BATS': 'R',
   'DOB': '08/10/1992',
   'THROWS': 'R',
   'HT': '6\' 4"',
   'DRAFTED': '2011, 1st (7) - ARI',
   'WT': '215',
   'TWITTER': '@ArchieBradley7'},
  {'first_name': 'Braden',
   'last_name': 'Shipley',
   'position': 'RHP',
   'Scouting Grades': 'Scouting grades: Fastball: 65 | Curveball: 55 | Changeup: 60 | Control: 60 | Overall: 55',
   'AGE': '31',
   'BATS': 'R',
   'DOB': '02/22/1992',
   'THROWS': 'R',
   'HT': '6\' 1"',
   'DRAFTED': '2013, 1st (15) - ARI',
   'WT': '190',
   'TWITTER': '@shipley25'},
  {'first_name': 'Chris',
   'last_name': 'Owings',
   'position': 'SS',
   'Scouting Grades': 'Hit: 55 | Power: 45 | Run: 55 | Arm: 50 | Field: 50 | Overall: 55',
   'AGE': '31',
   'BATS': 'R',
   'DOB': '08/12/1991',
   'THROWS': 'R',
   'HT': '5\' 10"',
   'DR

In [133]:
def list_to_df(ls):
    df = pd.DataFrame()
    for i in range(len(ls)):
        for j in range(len(ls[i])):
            player_info = ls[i][j]
            df = df.append(player_info, ignore_index = True)
    return df

In [134]:
df = list_to_df(crawling_list)

/var/folders/d7/8zsbg3r51rs_vl832mx18q_00000gn/T/ipykernel_89265/721942471.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(player_info, ignore_index = True)
/var/folders/d7/8zsbg3r51rs_vl832mx18q_00000gn/T/ipykernel_89265/721942471.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(player_info, ignore_index = True)
/var/folders/d7/8zsbg3r51rs_vl832mx18q_00000gn/T/ipykernel_89265/721942471.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(player_info, ignore_index = True)
/var/folders/d7/8zsbg3r51rs_vl832mx18q_00000gn/T/ipykernel_89265/721942471.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat 

first_name last_name position  \
8208       Jake       Alu    3B/2B   
8209    Gerardo  Carrillo      RHP   
8210       Drew    Millas        C   
8211     Darren     Baker       2B   
8212       Andy   Acevedo       OF   

                                        Scouting Grades AGE BATS         DOB  \
8208  Scouting grades: Hit: 50 | Power: 45 | Run: 40...  26    L  04/06/1997   
8209  Scouting grades: Fastball: 60 | Curveball: 50 ...  24    R  09/13/1998   
8210  Scouting grades: Hit: 40 | Power: 35 | Run: 45...  25    S  01/15/1998   
8211  Scouting grades: Hit: 50 | Power: 30 | Run: 55...  24    L  02/11/1999   
8212  Scouting grades: Hit: 55 | Power: 45 | Run: 50...  17    L  11/26/2005   

     THROWS      HT                 DRAFTED  ... OVERALL FASTBALL CURVEBALL  \
8208      R  5' 10"  2019, 24th (723) - WSH  ...     NaN      NaN       NaN   
8209      R   6' 1"                     NaN  ...     NaN      NaN       NaN   
8210      R   6' 0"   2019, 7th (224) - OAK  ...     NaN      NaN       NaN   
8211      R  5' 10"  2021, 10th (293) - WSH  ...     NaN      NaN       NaN   
8212      L   6' 1"                     NaN  ...     NaN      NaN       NaN   

     CHANGEUP CONTROL SLIDER CUTTER CURVE SPLITTER       
8208      NaN     NaN    NaN    NaN   NaN      NaN  NaN  
8209      NaN     NaN    NaN    NaN   NaN      NaN  NaN  
8210      NaN     NaN    NaN    NaN   NaN      NaN  NaN  
8211      NaN     NaN    NaN    NaN   NaN      NaN  NaN  
8212      NaN     NaN    NaN    NaN   NaN      NaN  NaN  

[5 rows x 29 columns]

In [137]:
df.to_csv('/Users/choeunsol/PAINS 23-1/프로젝트/tool/prospects_info.csv')

In [135]:
dr.quit()